In [1]:
# Processing libraries
import numpy as np
import pandas as pd
from matplotlib import pyplot as plt
from tqdm import tqdm
import random
import seaborn as sns
import pandas_ta as ta
import plotly.graph_objects as go
from scipy import stats
from backtesting import Backtest, Strategy
import seaborn as sns
from backtesting.lib import TrailingStrategy

In [2]:
df = pd.read_csv('data/appldata.csv')

# Preprocessing
df['Date'] = pd.to_datetime(df['Date'])
df.set_index('Date', inplace=True)
df = df.sort_values(by='Date', ascending=True)
df.tail()

Close    Open    High     Low     Vol. Change %
Date                                                        
2024-03-21  171.37  177.05  177.49  170.84  106.18M   -4.09%
2024-03-22  172.28  171.76  173.05  170.06   71.16M    0.53%
2024-03-25  170.85  170.37  171.94  169.46   54.21M   -0.83%
2024-03-26  169.71  170.01  171.41  169.65   57.22M   -0.67%
2024-03-27  173.31  170.30  173.58  170.14   59.11M    2.12%

In [8]:
# SMA Low and SMA High
sma_low = ta.sma(df["Close"], 50)
sma_high = ta.sma(df["Close"], 100)
sma_main = ta.sma(df["Close"], 200)

df["SMA_Low"] = sma_low
df["SMA_High"] = sma_high
df["SMA_Main"] = sma_main

df.tail()

Close    Open    High     Low     Vol. Change %   SMA_Low  \
Date                                                                     
2024-03-21  171.37  177.05  177.49  170.84  106.18M   -4.09%  182.6068   
2024-03-22  172.28  171.76  173.05  170.06   71.16M    0.53%  182.3286   
2024-03-25  170.85  170.37  171.94  169.46   54.21M   -0.83%  182.0338   
2024-03-26  169.71  170.01  171.41  169.65   57.22M   -0.67%  181.7096   
2024-03-27  173.31  170.30  173.58  170.14   59.11M    2.12%  181.5032   

            SMA_High   SMA_Main  Trend  
Date                                    
2024-03-21  185.3294  183.74450      0  
2024-03-22  185.3700  183.70985      0  
2024-03-25  185.3756  183.67500      0  
2024-03-26  185.3650  183.62070      0  
2024-03-27  185.3584  183.58245      0

In [4]:
fig = go.Figure()
fig.add_trace(go.Candlestick(
    x=df.index,
    open=df['Open'],
    high=df['High'],
    low=df['Low'],
    close=df['Close'],
    name='Candlesticks'
))
fig.add_trace(go.Scatter(
    x=df.index,
    y=df['SMA_Low'],
    line=dict(color='blue'),
    name='SMA_Low'
))
fig.add_trace(go.Scatter(
    x=df.index,
    y=df['SMA_High'],
    line=dict(color='orange'),
    name='SMA_High'
))
fig.add_trace(go.Scatter(
    x=df.index,
    y=df['SMA_Main'],
    line=dict(color='black'),
    name='SMA_Main'
))
fig.update_layout(
    xaxis_title='Date',
    yaxis_title='Price',
    xaxis_rangeslider_visible=False
)
fig.show()

In [5]:
def sma_trend(timestep, alpha):
    trend = [0] * len(df)
    for row in range(0, len(df)):
        slope = (df.iloc[row - 1].SMA_Main - df.iloc[row - timestep - 1].SMA_Main) / timestep
        if slope > alpha:
            trend[row] = 1 #uptrend
        if slope < -alpha:
            trend[row] = 2 #downtrend

    df['Trend'] = trend
    return trend

sma_trend(timestep=5, alpha=0.05)
df[df['Trend']!=0]

Close    Open    High     Low     Vol. Change %   SMA_Low  \
Date                                                                     
2012-04-02   22.09   21.49   22.10   21.44  598.35M    3.18%   18.8356   
2012-04-03   22.48   22.40   22.58   22.23  834.55M    1.77%   18.9800   
2012-04-04   22.30   22.30   22.35   22.04  572.98M   -0.80%   19.1258   
2012-04-05   22.63   22.39   22.67   22.26  641.28M    1.48%   19.2594   
2012-04-09   22.72   22.36   22.85   22.33  597.54M    0.40%   19.3962   
...            ...     ...     ...     ...      ...      ...       ...   
2024-02-22  184.37  183.48  184.96  182.46   52.29M    1.12%  189.1804   
2024-02-23  182.52  185.01  185.04  182.23   45.12M   -1.00%  188.9672   
2024-02-26  181.16  182.24  182.76  180.65   40.87M   -0.75%  188.6962   
2024-02-27  182.63  181.10  183.92  179.56   54.32M    0.81%  188.3896   
2024-02-28  181.42  182.51  183.12  180.13   48.95M   -0.66%  188.0558   

            SMA_High   SMA_Main  Trend  
Date                                    
2012-04-02   16.4935   15.02715      1  
2012-04-03   16.5732   15.08235      1  
2012-04-04   16.6550   15.13755      1  
2012-04-05   16.7437   15.19260      1  
2012-04-09   16.8335   15.24860      1  
...              ...        ...    ...  
2024-02-22  185.3280  183.68745      1  
2024-02-23  185.4411  183.73255      1  
2024-02-26  185.5152  183.77950      1  
2024-02-27  185.6175  183.82490      1  
2024-02-28  185.6951  183.86325      1  

[1298 rows x 10 columns]

In [13]:
# Create a figure
fig = go.Figure()

# Segment the DataFrame based on the 'Trend' column
df_up = df[df['Trend'] == 1]
df_down = df[df['Trend'] == 2]
df_none = df[df['Trend'] == 0]

# Add candlestick trace
fig.add_trace(go.Candlestick(
    x=df.index,
    open=df['Open'],
    high=df['High'],
    low=df['Low'],
    close=df['Close'],
    name='Candlesticks'
))

# Add traces for SMA_Main with different colors based on the trend
fig.add_trace(go.Scatter(
    x=df_up.index,
    y=df_up['SMA_Main'],
    mode='markers',  # Use 'markers' to avoid connecting lines
    marker=dict(color='green'),
    name='SMA_Main (Up)'
))

fig.add_trace(go.Scatter(
    x=df_down.index,
    y=df_down['SMA_Main'],
    mode='markers',  # Use 'markers' to avoid connecting lines
    marker=dict(color='red'),
    name='SMA_Main (Down)'
))

fig.add_trace(go.Scatter(
    x=df_none.index,
    y=df_none['SMA_Main'],
    mode='markers',  # Use 'markers' to avoid connecting lines
    marker=dict(color='black'),
    name='SMA_Main (None)'
))

# Update layout
fig.update_layout(
    xaxis_title='Date',
    yaxis_title='Price',
    xaxis_rangeslider_visible=False
)

# Show the figure
fig.show()

C:\Users\shive\AppData\Local\Temp\ipykernel_21924\2007010820.py:24: FutureWarning:

Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`

